In [1]:
"""
The aim of this script is to compare TRACEvar performance to common genetic tools (Fig. 2C-F). 
Tissue specific performance data and AUC plots created here, overall comparision is in the Methods_Comparison_Analysis.ipynb script.
"""

In [ ]:
import os
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn import metrics
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV
from sklearn.model_selection import StratifiedKFold
import pickle
import shap
from sklearn.metrics import precision_recall_curve
import matplotlib.pyplot as plt
import matplotlib
from sklearn.metrics import classification_report
from sklearn.metrics import roc_curve, auc
from sklearn.metrics import average_precision_score
import pickle
from scipy import interp

In [2]:
"------------------------------------------  Overlap cols ----------------------------------"

path = os.path.join('..', '..', 'Data', 'Relevant_Columns_Names_Edited_2.csv')
Relevant_Cols_df = pd.read_csv(path)
overlap_cols = Relevant_Cols_df['Feature'].tolist()
print(overlap_cols)


"------------------------------------------  Load Data ----------------------------------"

path = os.path.join('..', '..', 'Data', 'Full_Slim_Dataset_hg37-v1.6.csv')
Variants_data = pd.read_csv(path, engine='python') 
print(Variants_data)


path = os.path.join('..', '..', 'Results', 'Best_Parameters', 'Best_Parameters_New_17.csv')
Best_param = pd.read_csv(path, engine='python')
print(Best_param)


path_capice = os.path.join('..', '..', 'Data', 'CAPICE_hg37_VariantID.csv')
CAPICE_score = pd.read_csv(path_capice)


['Whole_Brain_diff_net_max', 'Whole_Blood_diff_net_max', 'Vagina_diff_net_max', 'Uterus_diff_net_max', 'Thyroid_diff_net_max', 'Testis_diff_net_max', 'Stomach_diff_net_max', 'Skin_-_Sun_Exposed_(Lower_leg)_diff_net_max', 'Skin_-_Not_Sun_Exposed_(Suprapubic)_diff_net_max', 'Prostate_diff_net_max', 'Pituitary_diff_net_max', 'Ovary_diff_net_max', 'Nerve_-_Tibial_diff_net_max', 'Muscle_-_Skeletal_diff_net_max', 'Minor_Salivary_Gland_diff_net_max', 'Lung_diff_net_max', 'Liver_diff_net_max', 'Heart_-_Left_Ventricle_diff_net_max', 'Heart_-_Atrial_Appendage_diff_net_max', 'Esophagus_-_Muscularis_diff_net_max', 'Esophagus_-_Mucosa_diff_net_max', 'Esophagus_-_Gastroesophageal_Junction_diff_net_max', 'Colon_-_Sigmoid_diff_net_max', 'Cells_-_Transformed_fibroblasts_diff_net_max', 'Cells_-_EBV-transformed_lymphocytes_diff_net_max', 'Breast_-_Mammary_Tissue_diff_net_max', 'Brain_-_Substantia_nigra_diff_net_max', 'Brain_-_Spinal_cord_(cervical_c-1)_diff_net_max', 'Brain_-_Putamen_(basal_ganglia)_diff

       VariationID   OMIMs                                 Manifested_Tissues  \
0           535972  613254  brain-0,kidney,Skin - Sun Exposed (Lower leg),...   
1           535875  613254  brain-0,kidney,Skin - Sun Exposed (Lower leg),...   
2           535979  613254  brain-0,kidney,Skin - Sun Exposed (Lower leg),...   
3           567376  613254  brain-0,kidney,Skin - Sun Exposed (Lower leg),...   
4           565912  613254  brain-0,kidney,Skin - Sun Exposed (Lower leg),...   
...            ...     ...                                                ...   
67963       873299     NaN                                                NaN   
67964       873211     NaN                                                NaN   
67965       873240     NaN                                                NaN   
67966       873216     NaN                                                NaN   
67967       915562     NaN                                                NaN   

      #Chr        Pos      

In [3]:
"----------------------------------- Create Scores DF -------------------------------------"

scores_y_columns = Variants_data.columns[Variants_data.columns.str.contains(pat = 'disease_causing')].tolist()
scores_y_columns = scores_y_columns + ['VariationID', 'PHRED', 'SIFTval', 'PolyPhenVal']
Scores_DF = pd.merge(Variants_data[scores_y_columns], CAPICE_score, on='VariationID', how='left')#VariationID
print('Scores_DF', Scores_DF)

Scores_DF['CAPICE'] = Scores_DF['CAPICE_Score'].apply(lambda x: x * 100)
Scores_DF['SIFT'] = Scores_DF['SIFTval'].apply(lambda x: x * 100)
Scores_DF['PolyPhen'] = Scores_DF['PolyPhenVal'].apply(lambda x: x * 100)


Scores_DF        Lung_disease_causing  Muscle - Skeletal_disease_causing  \
0                      True                              False   
1                      True                              False   
2                      True                              False   
3                      True                              False   
4                      True                              False   
...                     ...                                ...   
67963                 False                              False   
67964                 False                              False   
67965                 False                              False   
67966                 False                              False   
67967                 False                              False   

       Skin - Sun Exposed_disease_causing  \
0                                    True   
1                                    True   
2                                    True   
3                

In [4]:


"----------------------------------- Split data into non baiased folds -------------------------------------"

def split_data_on_genes(Variants_data, y):
    
    Genes_fraction = Variants_data['GeneID_y'][Variants_data[y] == True].value_counts(normalize=True)
    print(Genes_fraction.head(5))
    tissue = y.split('_')[0]
    Genes_as_factor = pd.DataFrame()
    Genes_as_factor['GeneID_y'] = Variants_data['GeneID_y'][Variants_data[y] == True].astype('category')
    Genes_as_factor["Gene_Categorical"] = Genes_as_factor["GeneID_y"].cat.codes
    Genes_fraction.columns = ['Fraction']
    return Genes_fraction, Genes_as_factor

def find_fold(Genes_fraction):
    
    Genes_fraction = Genes_fraction.sort_values()
    Genes_fraction = Genes_fraction.reset_index()
    Genes_fraction.columns = ['GeneID', 'Fraction']
    inds = Genes_fraction.index
    fold_list = []
    genes_list = []
    count_list = []
    fold = 0
    threshold = 0.1
    counter = 0
    for ind in inds:
        fraction = Genes_fraction.iloc[ind]['Fraction']
        gene = Genes_fraction.iloc[ind]['GeneID']

        counter += fraction

        if counter > threshold:
            fold += 1
            counter = 0
        if fraction >= threshold or fold > (1/threshold - 1):
            genes_list.append(gene)
            fold_list.append(None)
            break
        else:
            genes_list.append(gene)
            fold_list.append(fold)

    Fold_df = pd.DataFrame(list(zip(genes_list, fold_list)), columns=['GeneID', 'Fold'])
    Fold_merge = Genes_fraction.merge(Fold_df, on='GeneID', how='left')
    
    return Fold_merge

def random_split(Folds_df):
    
    threshold = 0.1
    Folds_df = Folds_df.sort_values('GeneID')
    Shafeled_df = Folds_df.sample(frac=1, random_state= 1234).reset_index(drop=True)
    inds = Shafeled_df.index
    new_fold = [None]*len(Folds_df)
    nan_inds = Shafeled_df[Shafeled_df['Fold'].isna()].index
    used_inds = [x for x in nan_inds]
    fold = 0
    for ind in inds:
        cuonter = 0
        fraction = Shafeled_df.iloc[ind]['Fraction']
        gene = Shafeled_df.iloc[ind]['GeneID']
        old_fold = Shafeled_df.iloc[ind]['Fold']
        cuonter += fraction
        if ind not in used_inds:
            new_fold[ind] = fold
            used_inds.append(ind)
            relevant_inds = [x for x in inds if x not in used_inds]
            for rel_ind in relevant_inds:
                fraction2 = Shafeled_df.iloc[rel_ind]['Fraction']
                if fraction2 + cuonter <= threshold:
                    cuonter += fraction2
                    new_fold[rel_ind] = fold
                    used_inds.append(rel_ind)
            fold += 1


    Shafeled_df['New_Fold'] = np.array(new_fold)
    print(Shafeled_df)
    folds = Shafeled_df['New_Fold'].unique()
    last_fold_num = Shafeled_df['New_Fold'].max()
    last_fold = Shafeled_df[Shafeled_df['New_Fold'] == last_fold_num]
    last_fold_sum = last_fold['Fraction'].sum()

    

    if last_fold_sum < 0.07:
        Shafeled_df['New_Fold'][Shafeled_df['New_Fold'] == last_fold_num] = last_fold_num - 1

        

    return Shafeled_df



y_columns = Variants_data.columns[Variants_data.columns.str.contains(pat = 'disease_causing')].tolist()
print(y_columns)
cols = overlap_cols 

"-------------------------- Data PreProcessing ------------------------"

def preprocessing_new(Relevant_data, y_columns, y):
    
    "------------- Remove nonrelevant coluns -------------------------"
    non_relevant_columns = ['VariationID', 'OMIMs', 'Manifested_Tissues', '#Chr', 'Pos', 'ConsDetail', 'motifEName', 'FeatureID', 'GeneName', 'CCDS', 'Intron', 'Exon', 'SIFTcat', 'PolyPhenCat', 'bStatistic', 'targetScan', 'dbscSNV-rf_score', 'oAA', 'Ref', 'nAA', 'Alt', 'Segway']# it will be good to replace oAA and nAA with blssuom64 matrix. What bStatistic doing?
    non_relevant_columns = non_relevant_columns + y_columns
    print(non_relevant_columns)

    relevant_columns = [x for x in cols if x not in non_relevant_columns and x in list(Variants_data)]
    relevant_columns.append(y)
    print(relevant_columns)
    Relevant_data = Variants_data[relevant_columns]
    print(Relevant_data)
    
    "---------------------- One Hot Columns -------------------------"
    
    one_hot_columns = ['Type', 'AnnoType', 'Consequence', 'Domain', 'Dst2SplType'] 

    one_hot = pd.get_dummies(Relevant_data[one_hot_columns])
    Relevant_data = Relevant_data.drop(one_hot_columns, axis=1)
    Relevant_data = Relevant_data.join(one_hot)
    
    "---------------------- Missing Values Imputation ---------------"
    
    special_imputation_cols = {'SIFTval':1, 'GC':0.42, 'CpG':0.02, 'priPhCons':0.115, 'mamPhCons':0.079, 'verPhCons':0.094,'priPhyloP':-0.033, 'mamPhyloP':-0.038, 'verPhyloP':0.017, 'GerpN':1.91, 'GerpS':-0.2}
    
    for cl in special_imputation_cols:
        Relevant_data[cl] = Relevant_data[cl].fillna(special_imputation_cols[cl])
        
    Relevant_data.fillna(0, inplace=True)
    
    return Relevant_data

"---------------------------------------- AUC drawing functions --------------------------------"

def plot_mean_auc(tprs, mean_fpr, aucs, dataset, color, ax):

    mean_tpr = np.mean(tprs, axis=0)
    mean_tpr[-1] = 1.0
    mean_auc = auc(mean_fpr, mean_tpr)
    std_auc = np.std(aucs)
    ax.plot(mean_fpr, mean_tpr, color=color,
             label= dataset+r' (auROC = %0.2f $\pm$ %0.2f)' % (mean_auc, std_auc),
             lw=2, alpha=.8)

def cadd_as_score_measurements(cadd_score_column, y):
    CADD_Scores_df = pd.concat([cadd_score_column, y], axis=1)#, ignore_index=True)
    CADD_Scores_df.columns = ['Pathogenicity_Score', 'tissue_specific_disease']
    CADD_Scores_df.dropna(subset=['Pathogenicity_Score'], inplace=True)

    print('CADD_Scores_df', CADD_Scores_df)

    max = 102
    ROC = np.zeros((max, 2))
    Precision_Recall = np.zeros((max, 2))
    average_precision = 0
    TPR_previuos = 0

    for i in range(max):
        # t = thresholds[i]
        t = i
        print('threshold: ', t)
        TP_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] >= t) & (CADD_Scores_df['tissue_specific_disease'] == True)])
        TN_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] < t) & (CADD_Scores_df['tissue_specific_disease'] == False)])
        FP_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] >= t) & (CADD_Scores_df['tissue_specific_disease'] == False)])
        FN_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] < t) & (CADD_Scores_df['tissue_specific_disease'] == True)])
        FPR_t = FP_t / float(FP_t + TN_t)
        ROC[i, 0] = FPR_t

        TPR_t = TP_t / float(TP_t + FN_t)  # = Recall
        ROC[i, 1] = TPR_t
        print('TP_t', TP_t)
        print('TN_t', TN_t)
        print('FP_t', FP_t)
        print('FN_t', FN_t)
        print('FPR_t', FPR_t)
        print('TPR_t', TPR_t)


        Precision_Recall[i, 0] = TPR_t
        try:
            precision = TP_t / float(TP_t + FP_t)
        except:
            precision = 0
        print('precision', precision)
        Precision_Recall[i, 1] = precision

        average_precision += (TPR_t - TPR_previuos) * precision
        TPR_previuos = TPR_t
    average_precision = average_precision * -1
    AUC = 0.
    for i in range(max-1):
        AUC += (ROC[i + 1, 0] - ROC[i, 0]) * (ROC[i + 1, 1] + ROC[i, 1])
    AUC *= -0.5
    roc_auc = metrics.auc(ROC[:,0], ROC[:,1])
    average_precision = metrics.auc(Precision_Recall[:,0], Precision_Recall[:,1])
    return Precision_Recall, average_precision, ROC, AUC

def sift_as_score_measurements(cadd_score_column, y):
    print('@', 'SIFT')
    CADD_Scores_df = pd.concat([cadd_score_column, y], axis=1)#, ignore_index=True)
    CADD_Scores_df.columns = ['Pathogenicity_Score', 'tissue_specific_disease']
    print('CADD_Scores_df', CADD_Scores_df)
    # thresholds = np.linspace(101, 1, 101)
    # print(thresholds)
    max = 102
    ROC = np.zeros((max, 2))
    Precision_Recall = np.zeros((max, 2))
    average_precision = 0
    TPR_previuos = 0

    for i in range(-1, max-1):
        t = i
        print('threshold: ', t)
        TP_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] <= t) & (CADD_Scores_df['tissue_specific_disease'] == True)])
        TN_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] > t) & (CADD_Scores_df['tissue_specific_disease'] == False)])
        FP_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] <= t) & (CADD_Scores_df['tissue_specific_disease'] == False)])
        FN_t = len(CADD_Scores_df[(CADD_Scores_df['Pathogenicity_Score'] > t) & (CADD_Scores_df['tissue_specific_disease'] == True)])
        FPR_t = FP_t / float(FP_t + TN_t)
        ROC[i+1, 0] = FPR_t

        TPR_t = TP_t / float(TP_t + FN_t)  # = Recall
        ROC[i+1, 1] = TPR_t
        print('TP_t', TP_t)
        print('TN_t', TN_t)
        print('FP_t', FP_t)
        print('FN_t', FN_t)
        print('FPR_t', FPR_t)
        print('TPR_t', TPR_t)


        Precision_Recall[i+1, 0] = TPR_t
        try:
            precision = TP_t / float(TP_t + FP_t)
        except:
            precision = 0
        print('precision', precision)
        Precision_Recall[i+1, 1] = precision

        average_precision += (TPR_t - TPR_previuos) * precision
        TPR_previuos = TPR_t
    average_precision = average_precision
    AUC = 0.
    for i in range(max-1):
        AUC += (ROC[i + 1, 0] - ROC[i, 0]) * (ROC[i + 1, 1] + ROC[i, 1])
    AUC *= 0.5
    roc_auc = metrics.auc(ROC[:,1], ROC[:,0])
    print('ROC')
    print(ROC)
    print('AUC')
    print(AUC)
    
    roc_auc = metrics.auc(ROC[:,0], ROC[:,1])
    average_precision = metrics.auc(Precision_Recall[:,0], Precision_Recall[:,1])
    
    return Precision_Recall, average_precision, ROC, AUC




['Lung_disease_causing', 'Muscle - Skeletal_disease_causing', 'Skin - Sun Exposed_disease_causing', 'Adipose - Subcutaneous_disease_causing', 'Artery - Aorta_disease_causing', 'Heart - Left Ventricle_disease_causing', 'Artery - Coronary_disease_causing', 'brain-0_disease_causing', 'Liver_disease_causing', 'Nerve - Tibial_disease_causing', 'Colon - Sigmoid_disease_causing', 'kidney_disease_causing', 'Heart - Atrial Appendage_disease_causing', 'Breast - Mammary Tissue_disease_causing', 'Uterus_disease_causing', 'Adipose - Visceral_disease_causing', 'Esophagus - Gastroesophageal Junction_disease_causing', 'Esophagus - Mucosa_disease_causing', 'brain-1_disease_causing', 'Skin - Not Sun Exposed_disease_causing', 'Artery - Tibial_disease_causing', 'Pituitary_disease_causing', 'Ovary_disease_causing', 'brain-3_disease_causing', 'Thyroid_disease_causing', 'Testis_disease_causing', 'Whole Blood_disease_causing', 'brain-2_disease_causing', 'brain_disease_causing']


In [5]:
import ast
from time import gmtime, strftime

"------------------------------ Train Model ---------------------------------------"
results_dict = {'Tissue':[], 'Data_set':[], 'Fold':[], 'ROC_AUC':[], 'PR_AUC':[]}
best_parameters_dict = {}
y_columns = ['Heart - Left Ventricle_disease_causing', 'brain_disease_causing', 'Lung_disease_causing', 'Muscle - Skeletal_disease_causing', 'Skin - Sun Exposed_disease_causing', 'Adipose - Subcutaneous_disease_causing', 'Artery - Aorta_disease_causing',  'Artery - Coronary_disease_causing', 'brain-0_disease_causing', 'Liver_disease_causing', 'Nerve - Tibial_disease_causing', 'Colon - Sigmoid_disease_causing', 'kidney_disease_causing', 'Heart - Atrial Appendage_disease_causing', 'Breast - Mammary Tissue_disease_causing', 'Uterus_disease_causing', 'Adipose - Visceral_disease_causing', 'Esophagus - Gastroesophageal Junction_disease_causing', 'Esophagus - Mucosa_disease_causing', 'brain-1_disease_causing', 'Skin - Not Sun Exposed_disease_causing', 'Artery - Tibial_disease_causing', 'Pituitary_disease_causing', 'Ovary_disease_causing', 'brain-3_disease_causing', 'Thyroid_disease_causing', 'Testis_disease_causing', 'Whole Blood_disease_causing', 'brain-2_disease_causing']

def compare_score_tissue(y):

    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(12, 8))
    tissue = y.replace("_disease_causing", "")

    if tissue.strip() in Best_param['Tissue'].unique():

        print("------------- ", y, " ------------------")
        pathogenic_proportion = Variants_data[y].value_counts(normalize=True)[True]
        print('Pathogenic_proportion', pathogenic_proportion)
        Relevant_data = preprocessing_new(Variants_data, y_columns, y)
        Genes_fraction = Variants_data['GeneID_y'][Variants_data[y] == True].value_counts(normalize=True)
        Genes_fraction, Genes_as_factor = split_data_on_genes(Variants_data, y)
        Folds_df = find_fold(Genes_fraction)
        print(Folds_df)
        Shafeled_Fold_df = random_split(Folds_df)

        folds_list = list(Shafeled_Fold_df['New_Fold'].unique())
        folds_list = [int(x) for x in folds_list if pd.notnull(x)]
        print('folds_list', folds_list)
        # break

        tprs = []
        aucs = []

        mean_fpr = np.linspace(0, 1, 100)
        y_real = []
        y_proba = []

        x_test_list = []
        y_test_list = []
        best_params_list = []
        num_genes = Variants_data['GeneID_y'][Variants_data[y]==True].nunique()
        if num_genes >= 20:
            for fold in folds_list:
                print(" Fold: ", fold)

                test_genes = Shafeled_Fold_df['GeneID'][Shafeled_Fold_df['New_Fold'] == fold].tolist()
                print('test_genes', test_genes)
                train_genes = Shafeled_Fold_df['GeneID'][Shafeled_Fold_df['New_Fold'] != fold].tolist()
                print('train_genes', train_genes)
                benign_genes = Variants_data['GeneID_y'][Variants_data[y] == False].tolist()
                print('benign_genes', len(benign_genes))

                Benign_data = Relevant_data[Relevant_data[y] == False]
                Pathogenic_test = Relevant_data[(Relevant_data[y] == True) & (Relevant_data['GeneID_y'].isin(test_genes))]
                Pathogenic_train = Relevant_data[(Relevant_data[y] == True) & (Relevant_data['GeneID_y'].isin(train_genes))]

                test_len =  len(Pathogenic_test)
                train_len = len(Pathogenic_train)
                test_fraction = test_len/(test_len+train_len)
                train_fraction = train_len/(test_len+train_len)
                print('test_fraction: ', test_fraction)
                print('train_fraction: ', train_fraction)

                X_train1, X_test1, y_train1, y_test1 = train_test_split(Benign_data, Benign_data[y], test_size=test_fraction, random_state=fold)

                X_train1 = X_train1[~X_train1['GeneID_y'].isin(test_genes)]
                X_test1 = X_test1[~X_test1['GeneID_y'].isin(train_genes)]
                y_train1 = y_train1[X_train1[~X_train1['GeneID_y'].isin(test_genes)].index]
                y_test1 = y_test1[X_test1[~X_test1['GeneID_y'].isin(train_genes)].index]

                relevant_cols2 = list(Pathogenic_train)
                relevant_cols = [x for x in relevant_cols2 if x != y and x != 'GeneID_y']
                print('relevant_cols', relevant_cols)


                X_train = pd.concat([X_train1[relevant_cols], Pathogenic_train[relevant_cols]])
                X_test = pd.concat([X_test1[relevant_cols], Pathogenic_test[relevant_cols]])
                y_train = pd.concat([y_train1, Pathogenic_train[y]])
                y_test = pd.concat([y_test1, Pathogenic_test[y]])

                X_train = X_train.sort_index()
                X_test = X_test.sort_index()
                y_train = y_train.sort_index()
                y_test = y_test.sort_index()

                print(y_test)


                best_parameters = Best_param['Best_Parameters'][(Best_param['Dataset'] == 'Full Trace')&(Best_param['Tissue'] == tissue.strip())&(Best_param['ML_Model'] == 'Random Forest')].values[0]
                best_parameters = ast.literal_eval(best_parameters)
                print(best_parameters)            
                model = RandomForestClassifier(**best_parameters)
                model.fit(X_train, y_train)

                y_pred = model.predict(X_test)  # predict the test data
                y_pred = pd.DataFrame(y_pred)
                predictions_proba = model.predict_proba(X_test)

                pred_true = predictions_proba[:, 1]
                clr = classification_report(y_test, y_pred, output_dict=True)
                print(clr)
                precision = clr['True']['precision']
                recall_1 = clr['True']['recall']
                f1_score = clr['True']['f1-score']
                print('@@@ ','precision:', precision, 'recall: ', recall_1, 'f1_score: ', f1_score)

                prec, recall, _ = precision_recall_curve(y_test, pred_true)  # pred[:, 1], pos_label=model.classes_[1]
                fpr, tpr, _ = roc_curve(y_test, pred_true)
                pr_auc1 = average_precision_score(y_test, pred_true)
                pr_auc1 =  metrics.auc(recall, prec)

                roc_auc = metrics.auc(fpr, tpr)
              
            
                data_set = 'Full TRACE'
                results_dict['Tissue'].append(tissue)
                results_dict['Data_set'].append(data_set)
                results_dict['Fold'].append(fold)
                results_dict['ROC_AUC'].append(roc_auc)
                results_dict['PR_AUC'].append(pr_auc1)

                tprs.append(interp(mean_fpr, fpr, tpr))
                tprs[-1][0] = 0.0
                aucs.append(roc_auc)
                y_real.append(y_test)
                y_proba.append(pred_true)

                x_test_list.append(X_test)
                y_test_list.append(y_test)
                # break
            if len(folds_list)>0:

                Precision_Recall, average_precision, ROC, AUC = cadd_as_score_measurements(Scores_DF['PHRED'], Scores_DF[y])
                ax2.plot(Precision_Recall[:, 0], Precision_Recall[:, 1], color='pink' ,label='%s (auPRC = %0.2f)' % ('CADD', average_precision))
                ax1.plot(ROC[:, 0], ROC[:, 1], color='pink', label='%s (auROC = %0.2f)' % ('CADD', AUC))

                results_dict['Tissue'].append(tissue)
                results_dict['Data_set'].append('CADD')
                results_dict['Fold'].append('All')
                results_dict['ROC_AUC'].append(AUC)
                results_dict['PR_AUC'].append(average_precision)

                Precision_Recall, average_precision, ROC, AUC = cadd_as_score_measurements(Scores_DF['CAPICE'], Scores_DF[y])
                ax2.plot(Precision_Recall[:, 0], Precision_Recall[:, 1], color='dimgray',label='%s (auPRC = %0.2f)' % ('CAPICE', average_precision))
                ax1.plot(ROC[:, 0], ROC[:, 1], color='dimgray', label='%s (auROC = %0.2f)' % ('CAPICE', AUC))

                results_dict['Tissue'].append(tissue)
                results_dict['Data_set'].append('CAPICE')
                results_dict['Fold'].append('All')
                results_dict['ROC_AUC'].append(AUC)
                results_dict['PR_AUC'].append(average_precision)
                print('------------------ Sift -----------------------')
                Precision_Recall, average_precision, ROC, AUC = sift_as_score_measurements(Scores_DF['SIFT'], Scores_DF[y])
                ax2.plot(Precision_Recall[:, 0], Precision_Recall[:, 1], color='forestgreen',label='%s (auPRC = %0.2f)' % ('SIFT', average_precision))
                ax1.plot(ROC[:, 0], ROC[:, 1], color='forestgreen', label='%s (auROC = %0.2f)' % ('SIFT', AUC))

                results_dict['Tissue'].append(tissue)
                results_dict['Data_set'].append('SIFT')
                results_dict['Fold'].append('All')
                results_dict['ROC_AUC'].append(AUC)
                results_dict['PR_AUC'].append(average_precision)

                Precision_Recall, average_precision, ROC, AUC = cadd_as_score_measurements(Scores_DF['PolyPhen'], Scores_DF[y])
                ax2.plot(Precision_Recall[:, 0], Precision_Recall[:, 1], color='darkorange',label='%s (auPRC = %0.2f)' % ('PolyPhen', average_precision))
                ax1.plot(ROC[:, 0], ROC[:, 1], color='darkorange', label='%s  (auROC = %0.2f)' % ('PolyPhen', AUC))

                results_dict['Tissue'].append(tissue)
                results_dict['Data_set'].append('PolyPhen')
                results_dict['Fold'].append('All')
                results_dict['ROC_AUC'].append(AUC)
                results_dict['PR_AUC'].append(average_precision)


                full_interp_list = tprs
                full_auc_list = aucs

                plot_mean_auc(full_interp_list, mean_fpr, full_auc_list, 'TRACEvar', 'blue', ax1)

                ax1.plot([0, 1], [0, 1], 'r--')

                ax1.set_xlabel('1-Specificity(False Positive Rate)')
                ax1.set_ylabel('Sensitivity(True Positive Rate)')
                ax1.set_title('Receiver Operating Characteristic')
                ax1.legend(loc="lower right", fontsize='small')

                fig.suptitle(tissue)



                y_real_trace = np.concatenate(y_real)
                y_proba_trace = np.concatenate(y_proba)

                precision_trace, recall_trace, _ = precision_recall_curve(y_real_trace, y_proba_trace)

                plt.plot(recall_trace, precision_trace, color='blue', label=r'TRACEvar (mean auPRC = %0.2f)' % (average_precision_score(y_real_trace, y_proba_trace)), lw=2, alpha=.8)
                ax2.axhline(y=pathogenic_proportion, color='red', linestyle='--',
                            label=r'Pathogenic variants frequency = %0.3f' % (pathogenic_proportion))
                ax2.set_xlabel('Recall')
                ax2.set_ylabel('Precision')
                ax2.set_title('Precision-Recall curve')
                ax2.legend(loc="lower right", fontsize='small')
                path = os.path.join('..', '..', 'Results', 'Slim Model Comparison3',  tissue + '_Compare_Scores_Slim_Model_Docker.pdf')
                plt.savefig(path)
                plt.close()
    #               plt.show()
                Results = pd.DataFrame.from_dict(results_dict)
                path = os.path.join('..', '..', 'Results', 'Slim Model Comparison3',  tissue + '_Compare_Scores_Slim_Model_Docker.csv')
                Results.to_csv(path, index=None)
            
    return tissue, strftime("%Y-%m-%d %H:%M:%S", gmtime())


In [6]:
import multiprocessing as mp

def driver_func_shap():
    PROCESSES = 20
    df_list = []
    
    with mp.Pool(PROCESSES) as pool:
        results = [pool.apply_async(compare_score_tissue, (y,)) for y in y_columns]
        for r in results:
            results_tuple = r.get(timeout=None)
            print('@', results_tuple[0], ' finished', results_tuple[1])

if __name__ == '__main__':
    print(strftime("%Y-%m-%d %H:%M:%S", gmtime()))
    driver_func_shap()    
    

2023-01-02 08:39:29
-------------  Heart - Left Ventricle_disease_causing  ------------------
-------------  Muscle - Skeletal_disease_causing  ------------------
-------------  Lung_disease_causing  ------------------
-------------  brain_disease_causing  ------------------
-------------  brain-1_disease_causing  ------------------
Pathogenic_proportion 0.02863112052730697
['VariationID', 'OMIMs', 'Manifested_Tissues', '#Chr', 'Pos', 'ConsDetail', 'motifEName', 'FeatureID', 'GeneName', 'CCDS', 'Intron', 'Exon', 'SIFTcat', 'PolyPhenCat', 'bStatistic', 'targetScan', 'dbscSNV-rf_score', 'oAA', 'Ref', 'nAA', 'Alt', 'Segway', 'Heart - Left Ventricle_disease_causing', 'brain_disease_causing', 'Lung_disease_causing', 'Muscle - Skeletal_disease_causing', 'Skin - Sun Exposed_disease_causing', 'Adipose - Subcutaneous_disease_causing', 'Artery - Aorta_disease_causing', 'Artery - Coronary_disease_causing', 'brain-0_disease_causing', 'Liver_disease_causing', 'Nerve - Tibial_disease_causing', 'Colo

Pathogenic_proportion 0.007120998116760828
['VariationID', 'OMIMs', 'Manifested_Tissues', '#Chr', 'Pos', 'ConsDetail', 'motifEName', 'FeatureID', 'GeneName', 'CCDS', 'Intron', 'Exon', 'SIFTcat', 'PolyPhenCat', 'bStatistic', 'targetScan', 'dbscSNV-rf_score', 'oAA', 'Ref', 'nAA', 'Alt', 'Segway', 'Heart - Left Ventricle_disease_causing', 'brain_disease_causing', 'Lung_disease_causing', 'Muscle - Skeletal_disease_causing', 'Skin - Sun Exposed_disease_causing', 'Adipose - Subcutaneous_disease_causing', 'Artery - Aorta_disease_causing', 'Artery - Coronary_disease_causing', 'brain-0_disease_causing', 'Liver_disease_causing', 'Nerve - Tibial_disease_causing', 'Colon - Sigmoid_disease_causing', 'kidney_disease_causing', 'Heart - Atrial Appendage_disease_causing', 'Breast - Mammary Tissue_disease_causing', 'Uterus_disease_causing', 'Adipose - Visceral_disease_causing', 'Esophagus - Gastroesophageal Junction_disease_causing', 'Esophagus - Mucosa_disease_causing', 'brain-1_disease_causing', 'Skin

-------------  brain-2_disease_causing  ------------------
Pathogenic_proportion 0.007886064030131828
['VariationID', 'OMIMs', 'Manifested_Tissues', '#Chr', 'Pos', 'ConsDetail', 'motifEName', 'FeatureID', 'GeneName', 'CCDS', 'Intron', 'Exon', 'SIFTcat', 'PolyPhenCat', 'bStatistic', 'targetScan', 'dbscSNV-rf_score', 'oAA', 'Ref', 'nAA', 'Alt', 'Segway', 'Heart - Left Ventricle_disease_causing', 'brain_disease_causing', 'Lung_disease_causing', 'Muscle - Skeletal_disease_causing', 'Skin - Sun Exposed_disease_causing', 'Adipose - Subcutaneous_disease_causing', 'Artery - Aorta_disease_causing', 'Artery - Coronary_disease_causing', 'brain-0_disease_causing', 'Liver_disease_causing', 'Nerve - Tibial_disease_causing', 'Colon - Sigmoid_disease_causing', 'kidney_disease_causing', 'Heart - Atrial Appendage_disease_causing', 'Breast - Mammary Tissue_disease_causing', 'Uterus_disease_causing', 'Adipose - Visceral_disease_causing', 'Esophagus - Gastroesophageal Junction_disease_causing', 'Esophagus 

['Whole_Brain_diff_net_max', 'Whole_Blood_diff_net_max', 'Vagina_diff_net_max', 'Uterus_diff_net_max', 'Thyroid_diff_net_max', 'Testis_diff_net_max', 'Stomach_diff_net_max', 'Skin_-_Sun_Exposed_(Lower_leg)_diff_net_max', 'Skin_-_Not_Sun_Exposed_(Suprapubic)_diff_net_max', 'Prostate_diff_net_max', 'Pituitary_diff_net_max', 'Ovary_diff_net_max', 'Nerve_-_Tibial_diff_net_max', 'Muscle_-_Skeletal_diff_net_max', 'Minor_Salivary_Gland_diff_net_max', 'Lung_diff_net_max', 'Liver_diff_net_max', 'Heart_-_Left_Ventricle_diff_net_max', 'Heart_-_Atrial_Appendage_diff_net_max', 'Esophagus_-_Muscularis_diff_net_max', 'Esophagus_-_Mucosa_diff_net_max', 'Esophagus_-_Gastroesophageal_Junction_diff_net_max', 'Colon_-_Sigmoid_diff_net_max', 'Cells_-_Transformed_fibroblasts_diff_net_max', 'Cells_-_EBV-transformed_lymphocytes_diff_net_max', 'Breast_-_Mammary_Tissue_diff_net_max', 'Brain_-_Substantia_nigra_diff_net_max', 'Brain_-_Spinal_cord_(cervical_c-1)_diff_net_max', 'Brain_-_Putamen_(basal_ganglia)_diff

['Whole_Brain_diff_net_max', 'Whole_Blood_diff_net_max', 'Vagina_diff_net_max', 'Uterus_diff_net_max', 'Thyroid_diff_net_max', 'Testis_diff_net_max', 'Stomach_diff_net_max', 'Skin_-_Sun_Exposed_(Lower_leg)_diff_net_max', 'Skin_-_Not_Sun_Exposed_(Suprapubic)_diff_net_max', 'Prostate_diff_net_max', 'Pituitary_diff_net_max', 'Ovary_diff_net_max', 'Nerve_-_Tibial_diff_net_max', 'Muscle_-_Skeletal_diff_net_max', 'Minor_Salivary_Gland_diff_net_max', 'Lung_diff_net_max', 'Liver_diff_net_max', 'Heart_-_Left_Ventricle_diff_net_max', 'Heart_-_Atrial_Appendage_diff_net_max', 'Esophagus_-_Muscularis_diff_net_max', 'Esophagus_-_Mucosa_diff_net_max', 'Esophagus_-_Gastroesophageal_Junction_diff_net_max', 'Colon_-_Sigmoid_diff_net_max', 'Cells_-_Transformed_fibroblasts_diff_net_max', 'Cells_-_EBV-transformed_lymphocytes_diff_net_max', 'Breast_-_Mammary_Tissue_diff_net_max', 'Brain_-_Substantia_nigra_diff_net_max', 'Brain_-_Spinal_cord_(cervical_c-1)_diff_net_max', 'Brain_-_Putamen_(basal_ganglia)_diff

...

precision 0.03195506923598335
threshold:  28
TP_t 329
TN_t 56513
FP_t 9926
FN_t 193
FPR_t 0.14940020168876714
TPR_t 0.6302681992337165
precision 0.032081911262798635
threshold:  29
TP_t 326
TN_t 56595
FP_t 9844
FN_t 196
FPR_t 0.14816598684507593
TPR_t 0.6245210727969349
precision 0.032055063913470995
threshold:  30
TP_t 320
TN_t 56658
FP_t 9781
FN_t 202
FPR_t 0.1472177486115083
TPR_t 0.6130268199233716
precision 0.03168003168003168
threshold:  31
TP_t 318
TN_t 56720
FP_t 9719
FN_t 204
FPR_t 0.1462845617784735
TPR_t 0.6091954022988506
precision 0.03168277373717246
threshold:  32
TP_t 316
TN_t 56791
FP_t 9648
FN_t 206
FPR_t 0.1452159123406433
TPR_t 0.6053639846743295
precision 0.031714171015656364
threshold:  33
TP_t 313
TN_t 56858
FP_t 9581
FN_t 209
FPR_t 0.1442074685049444
TPR_t 0.5996168582375478
precision 0.03163533454618961
threshold:  34
TP_t 309
TN_t 56921
FP_t 9518
FN_t 213
FPR_t 0.14325923027137674
TPR_t 0.5919540229885057
precision 0.03144398086903429
threshold:  35
TP_t 305
TN

FN_t 382
FPR_t 0.08788512771113352
TPR_t 0.2681992337164751
precision 0.023415286837263755
threshold:  89
TP_t 138
TN_t 60745
FP_t 5694
FN_t 384
FPR_t 0.08570267463387468
TPR_t 0.26436781609195403
precision 0.023662551440329218
threshold:  90
TP_t 135
TN_t 60867
FP_t 5572
FN_t 387
FPR_t 0.0838664037688707
TPR_t 0.25862068965517243
precision 0.02365516032942001
threshold:  91
TP_t 132
TN_t 61026
FP_t 5413
FN_t 390
FPR_t 0.08147323108415239
TPR_t 0.25287356321839083
precision 0.02380522993688007
threshold:  92
TP_t 127
TN_t 61213
FP_t 5226
FN_t 395
FPR_t 0.07865861918451512
TPR_t 0.24329501915708812
precision 0.023725014010835047
threshold:  93
TP_t 124
TN_t 61416
FP_t 5023
FN_t 398
FPR_t 0.07560318487635274
TPR_t 0.23754789272030652
precision 0.024091703905187487
threshold:  94
TP_t 116
TN_t 61697
FP_t 4742
FN_t 406
FPR_t 0.07137374132663045
TPR_t 0.2222222222222222
precision 0.02387813915191437
threshold:  95
TP_t 106
TN_t 61982
FP_t 4457
FN_t 416
FPR_t 0.06708409217477686
TPR_t 0.2030

precision 0.01786735277301315
threshold:  43
TP_t 250
TN_t 3187
FP_t 13817
FN_t 1
FPR_t 0.8125735121147966
TPR_t 0.9960159362549801
precision 0.01777209070875098
threshold:  44
TP_t 250
TN_t 3114
FP_t 13890
FN_t 1
FPR_t 0.8168666196189132
TPR_t 0.9960159362549801
precision 0.01768033946251768
threshold:  45
TP_t 250
TN_t 3048
FP_t 13956
FN_t 1
FPR_t 0.8207480592801694
TPR_t 0.9960159362549801
precision 0.01759819794453048
threshold:  46
TP_t 250
TN_t 2969
FP_t 14035
FN_t 1
FPR_t 0.8253940249353093
TPR_t 0.9960159362549801
precision 0.01750087504375219
threshold:  47
TP_t 250
TN_t 2905
FP_t 14099
FN_t 1
FPR_t 0.829157845212891
TPR_t 0.9960159362549801
precision 0.017422816921039794
threshold:  48
TP_t 250
TN_t 2852
FP_t 14152
FN_t 1
FPR_t 0.8322747588802635
TPR_t 0.9960159362549801
precision 0.01735870018053048
threshold:  49
TP_t 250
TN_t 2787
FP_t 14217
FN_t 1
FPR_t 0.8360973888496824
TPR_t 0.9960159362549801
precision 0.017280707817792215
threshold:  50
TP_t 250
TN_t 2713
FP_t 14291


 [1.         1.        ]]
AUC
0.7655411053972775
CADD_Scores_df        Pathogenicity_Score  tissue_specific_disease
25                    99.9                    False
29                    98.6                    False
30                    99.8                    False
32                    99.9                    False
33                    94.5                    False
...                    ...                      ...
67945                  5.3                    False
67946                  1.5                    False
67958                 16.8                    False
67959                 67.1                    False
67967                 50.9                    False

[17317 rows x 2 columns]
threshold:  0
TP_t 251
TN_t 0
FP_t 17066
FN_t 0
FPR_t 1.0
TPR_t 1.0
precision 0.01449442744124271
threshold:  1
TP_t 248
TN_t 4875
FP_t 12191
FN_t 3
FPR_t 0.7143443103246221
TPR_t 0.9880478087649402
precision 0.019937293994694107
threshold:  2
TP_t 248
TN_t 5799
FP_t 11267
FN_t 3
FPR_t

precision 0.0326214160327677
threshold:  57
TP_t 222
TN_t 10483
FP_t 6583
FN_t 29
FPR_t 0.3857377241298488
TPR_t 0.8844621513944223
precision 0.032623071271124175
threshold:  58
TP_t 221
TN_t 10525
FP_t 6541
FN_t 30
FPR_t 0.3832766904957225
TPR_t 0.8804780876494024
precision 0.03268263827270038
threshold:  59
TP_t 221
TN_t 10548
FP_t 6518
FN_t 30
FPR_t 0.38192898160084376
TPR_t 0.8804780876494024
precision 0.03279418311322155
threshold:  60
TP_t 219
TN_t 10581
FP_t 6485
FN_t 32
FPR_t 0.3799953123168874
TPR_t 0.8725099601593626
precision 0.03266706443914081
threshold:  61
TP_t 218
TN_t 10613
FP_t 6453
FN_t 33
FPR_t 0.3781202390718387
TPR_t 0.8685258964143426
precision 0.03267875880677559
threshold:  62
TP_t 216
TN_t 10654
FP_t 6412
FN_t 35
FPR_t 0.3757178014766202
TPR_t 0.8605577689243028
precision 0.032589016294508145
threshold:  63
TP_t 216
TN_t 10704
FP_t 6362
FN_t 35
FPR_t 0.3727879995312317
TPR_t 0.8605577689243028
precision 0.0328367284889024
threshold:  64
TP_t 215
TN_t 10749
FP_